In [6]:
from skewPy import SkewT
import matplotlib.pyplot as plt
import numpy as np
import seaborn as sns
import pandas as pd
import glob

#plt.close('all')

# Main folder where the reading is done; creates list of all current soundings
read_folder = '/Volumes/cruiseshare/Soundings/Thompson/edt/'
file_list = sorted(glob.glob(read_folder + '*'))
print('List of soundings: ', file_list)
print('Most current sounding: ', file_list[-1])

# Read the most recent one
S1 = SkewT.Sounding(filename=file_list[-1], fmt='PISTON_EDT', init_plot=1)


List of soundings:  ['/Volumes/cruiseshare/Soundings/Thompson/edt/edt_20180820_2335.txt', '/Volumes/cruiseshare/Soundings/Thompson/edt/edt_20180821_0530.txt', '/Volumes/cruiseshare/Soundings/Thompson/edt/edt_20180821_1235.txt', '/Volumes/cruiseshare/Soundings/Thompson/edt/edt_20180821_1733.txt', '/Volumes/cruiseshare/Soundings/Thompson/edt/edt_20180821_2333.txt', '/Volumes/cruiseshare/Soundings/Thompson/edt/edt_20180822_0523.txt', '/Volumes/cruiseshare/Soundings/Thompson/edt/edt_20180822_1128.txt', '/Volumes/cruiseshare/Soundings/Thompson/edt/edt_20180822_1724.txt', '/Volumes/cruiseshare/Soundings/Thompson/edt/edt_20180822_2328.txt', '/Volumes/cruiseshare/Soundings/Thompson/edt/edt_20180823_0226.txt', '/Volumes/cruiseshare/Soundings/Thompson/edt/edt_20180823_0526.txt', '/Volumes/cruiseshare/Soundings/Thompson/edt/edt_20180823_0827.txt', '/Volumes/cruiseshare/Soundings/Thompson/edt/edt_20180823_1128.txt', '/Volumes/cruiseshare/Soundings/Thompson/edt/edt_20180823_1426.txt', '/Volumes/cru

In [14]:
# Use to plot multiple soundings on the same file; the indexing on files_list
# within the for loop controls what is displayed. Need to update to have legend
# and more robust color scheme

S1 = SkewT.Sounding(data={}, fmt='PISTON_EDT')
S1.make_skewt_axes()
data_set = ()
date_list = ()

clrs = sns.color_palette('Blues', len(file_list))

for file_name,idx in zip(file_list[0:-1], np.arange(len(file_list))+1):
    S1.readfile(file_name)
    #S1.add_profile(color=clrs[-idx], bloc=.6 + .2*idx, bcol=clrs[-idx])
    data_set = np.append(data_set, S1.data)
    date_list = np.append(date_list, S1.sounding_date)


Need to shift the columns
Need to shift the columns
Need to shift the columns
Need to shift the columns
Need to shift the columns
Need to shift the columns
Need to shift the columns
Need to shift the columns
Need to shift the columns
Need to shift the columns
Need to shift the columns
Need to shift the columns
Need to shift the columns
Need to shift the columns
Need to shift the columns
Need to shift the columns
Need to shift the columns


In [15]:
# Function which takes a dictionary data_in and interpolate a key data_str onto heights
# goal_hghts. Might update to have automatically cycle through dictionary keys rather than
# take data_str, but not too many variables of interest to read
def interp_all(data_str, goal_hghts, data_in):
    data_out = np.empty([len(goal_hghts), len(data_in)])
    for i in range(len(data_in)):
        #print(data_in[i]['hght'])
        #print(data_in[i][data_str])
        data_out[:,i] = np.interp(goal_hghts, data_in[i]['hght'], data_in[i][data_str])
    return(data_out)

# Sets up goal heights up to 20km and interpolate tempa nd dewpt
z = np.linspace(0, np.min([data_set[_]['hght'][-1] for _ in range(len(data_set))])+100, 2000)
temp = interp_all('temp', z, data_set)
dwpt = interp_all('dwpt', z, data_set)
pres = interp_all('pres', z, data_set)



# Calculates zonal and meridional wind from the speed and direction
u = np.empty([len(z), len(data_set)])
v = np.empty(u.shape)

for i in range(len(data_set)):
    utemp = data_set[i]['sknt']*np.cos(np.radians(270-data_set[i]['drct']))
    vtemp = data_set[i]['sknt']*np.sin(np.radians(270-data_set[i]['drct']))
    utemp = np.interp(z, data_set[i]['hght'], utemp)
    vtemp = np.interp(z, data_set[i]['hght'], vtemp)
    u[:,i] = utemp
    v[:,i] = vtemp
#print(u)

# Calculates relative humidity; might also read in and compare if in sounding
relh = SkewT.RH(temp, dwpt)


In [16]:
Smean = {}
for key in S1.data.keys():
    #print(key)
    for i in range(len(data_set)):
        tmp = data_set[i][key]
        tmp = np.interp(z, data_set[i]['hght'], data_set[i][key])
        #print(temp)
        if i == 0:
            Smean[key] = tmp
        else:
            Smean[key] = (Smean[key] + tmp)/2



In [17]:
mean_sounding = SkewT.Sounding(data=Smean)


In [18]:
mean_sounding.plot_skewt(title='Mean sounding')


p_lcl =  947.603687743
lcl_height =  574.636268134
[  60  209  354  495  633  767  897 1024 1146 1263 1376 1484 1589 1689 1787
 1886 1986 1999]
2000


In [19]:
z.shape

(2000,)

In [20]:
# Makes plots of time series of data

fig = plt.figure()

ax1 = fig.add_subplot(3,1,1)
ax2 = fig.add_subplot(3,1,2)
ax3 = fig.add_subplot(3,1,3)

cf = ax1.contourf(date_list, z, temp, np.arange(10,35,.5),cmap='RdBu_r')
plt.colorbar(cf, ax=ax1)
ax1.set_ylim([0, 500])
ax1.set_title('Temperature (C)')

ax2.plot(date_list, np.min(temp, 0))
ax2.set_title('Cold point tropopause (C)')

melting_level = np.empty(len(data_set))
for i in range(len(data_set)):
          melting_level[i] = data_set[i]['hght'][np.argmin(abs(data_set[i]['temp']-0))]

ax3.plot(date_list, melting_level/1000)
ax3.set_title('Melting Level (km)')

fig.tight_layout()
plt.show()

plt.figure()
plt.contourf(date_list, z, u, cmap='RdBu_r')
plt.title('Zonal wind (knots)')
plt.colorbar()
plt.show()

plt.figure()
plt.contourf(date_list, z, v, cmap='RdBu_r')
plt.title('Meridional wind (knots)')
plt.colorbar()
plt.show()

plt.figure()
plt.contourf(date_list, z, relh, np.linspace(80, 100, 25), cmap='Greens', extend='both')
plt.title('Relative humidity (%)')
plt.colorbar()
plt.show()





In [21]:
temp_anom = np.empty(temp.shape)
for i in range(temp.shape[1]):
    temp_anom[:,i] = temp[:, i] - temp.mean(1) 
    
plt.figure()
plt.contourf(date_list, z, temp_anom , cmap='RdBu_r')
plt.colorbar()
plt.title('Temperature Anomaly (C)')

plt.tight_layout()
plt.show()

In [22]:
temp_anom

array([[ 0.64705882,  1.14705882,  0.74705882, ..., -0.75294118,
        -0.65294118, -0.35294118],
       [ 0.57614288,  1.13757643,  0.76741974, ..., -0.70746904,
        -0.6067762 , -0.40983468],
       [ 0.47047108,  1.12344672,  0.79775953, ..., -0.63971105,
        -0.53798582, -0.49461163],
       ..., 
       [-4.50259673, -0.50259673, -1.00259673, ..., -0.70259673,
        -2.80259673,  0.79740327],
       [-4.21912725, -0.52270304, -1.10564358, ..., -0.82270304,
        -2.82270304,  0.77729696],
       [-3.93399561, -0.45725143, -1.15725143, ..., -0.85725143,
        -2.75725143,  0.74274857]])

In [23]:
plt.figure()
plt.plot(temp.mean(1), z)
plt.title('Mean temp (C)')
plt.show()

plt.figure()
plt.plot(dwpt.mean(1), z)
plt.title('Mean dew point temp (C)')
plt.show()

In [24]:
from skewPy.thermodynamics import Rs_da, Rs_v, Cp_da, Epsilon
theta = (temp+273.15)*(1000/pres)**(Rs_da/Cp_da)

In [25]:
plt.figure()
plt.contourf(date_list, z, theta, cmap='RdBu_r')
plt.colorbar(cf, ax=ax1)
plt.ylim([0, 5000])
plt.title('Potential Temperature (K)')
plt.show()

plt.figure()
plt.contourf(date_list, z, relh, np.linspace(90, 100, 25), cmap='Greens', extend='both')
plt.title('Relative humidity (%)')
plt.ylim([0, 5000])
plt.colorbar()
plt.show()

plt.figure()
plt.contourf(date_list, z, u, np.arange(-15, 30, 5), cmap='RdBu_r')
plt.title('Zonal wind (knots)')
plt.ylim([0, 5000])
plt.colorbar()
plt.show()

plt.figure()
plt.contourf(date_list, z, v, np.arange(-15, 30, 5), cmap='RdBu_r')
plt.title('Meridional wind (knots)')
plt.ylim([0, 5000])
plt.colorbar()
plt.show()




In [42]:
theta.shape

(2000,)

In [33]:
S1.data['temp'][1::]

array([ 27.5,  27.4,  27.3, ..., -58. , -58. , -57.9])